# Project 12: Spatial fairness in urban environments <br>

In [1]:
import geopandas as gpd
import folium
import numpy as np
import networkx as nx
import pandas as pd
import itertools
import warnings
import sumolib
import os
#import openrouteservice as ors
from sklearn.preprocessing import MinMaxScaler

from shapely.geometry import LineString, Point

import warnings
warnings.filterwarnings("ignore")

from plot_utils import edges_to_gps_list, plot_paths, plot_bar_paths_cost
from routing_utils import from_sumo_to_igraph_network
from routing_algorithms import *
import matplotlib.pyplot as plt

attribute = 'traveltime'

### Utility <br>
Functions to improve readability

In [2]:
# modified version of the function of GiulianoCornacchia from the github,
# the only change is that the dataframe has one column for the edge id and one column for the geometry
def gdf_from_sumo_network(sumo_road_network, crs="EPSG:4326", edge_list=None):
    edges_to_plot = sumo_road_network.getEdges()
        
    list_line_strings = []
    list_ids = [] 

    for edge in edges_to_plot: 
        list_ids.append(edge.getID())      
        edge_gps_list = [sumo_road_network.convertXY2LonLat(x[0], x[1]) for x in edge.getShape()]
        list_line_strings.append(LineString(edge_gps_list))

    df_net = gpd.GeoDataFrame(data = list_ids, geometry=list_line_strings, crs="EPSG:4326") 

    df_net.columns = ['id', 'geometry']
    return df_net 

In [3]:
# function to print the correct row for the file xml
# path: tuple/list of edges
# i: identifier for the row
# type: type of trip, in this case if it is toward the city center or towards a random edge
# return: row ready to be written in the file
def path_to_xml(path, i, type):
    edges = ''
    depart = np.random.randint(0, 200)

    for e in path:
        edges+= str(e.getID()) + ' '

    s = '<vehicle id="'+type+str(i)+'" type="veh_passenger" depart="0" departLane="best"> <route edges="'+ edges +'"/> </vehicle> '
    return s

# function to print the correct row for the file xml
# path: list of edges ids
# i: identifier for the row
# type: type of trip, in this case if it is toward the city center or towards a random edge
# return: row ready to be written in the file
def list_to_xml(path, i, type):
    edges = ''
    depart = np.random.randint(0, 200)

    for e in path:
        edges+= str(e) + ' '

    s = '<vehicle id="'+type+str(i)+'" type="veh_passenger" depart="0" departLane="best"> <route edges="'+ edges +'"/> </vehicle> '
    return s

In [4]:
# create a blank map for the city of Leuven
def Leuven_map():
    point = (50.849738563227824, 4.644786576420597)
    m = folium.Map(location=point, zoom_start = 12)
    return m

m = Leuven_map()

## Data

In [5]:
# Open the hubs dataframe
url = 'https://storageaccount11111111.blob.core.windows.net/container1/Leuven/hub_data_leuven/mobility_hubs.gpkg'
hubs = gpd.read_file(url).to_crs('epsg:4326')[['nr', 'naam punt', 'geometry']]
folium.GeoJson(hubs).add_to(m)

In [6]:
# Open the zone dataframe
zones_leuven = gpd.read_file('https://storageaccount11111111.blob.core.windows.net/container1/Leuven/socio_demographic_data/leuven_statsec.gpkg')
zones_leuven = zones_leuven.to_crs('epsg:4326')[['CODSEC', 'geometry']]
folium.GeoJson(zones_leuven).add_to(m)

In [7]:
# NORMALIZATION BY AREA
# area for zones in squared meters
utm = zones_leuven.estimate_utm_crs()
zones_leuven['area'] = zones_leuven.to_crs(utm).area

scaler = MinMaxScaler()
zones_leuven['area'] = scaler.fit_transform(np.array(zones_leuven['area']).reshape(-1,1))

In [8]:
# road network from the sumo network
#
# python tools\net\net2geojson.py -n C:\Users\and99\Desktop\Geospatial-project\Sumo\osm.net.xml\osm.net.xml -o road_network.geojson
# road_net = gpd.read_file('road_network_pedestrian.geojson')
#
# build the network, the gdf and the graph directly from the sumo configuration
net = sumolib.net.readNet(os.getcwd()+'/Sumo/osm.net.xml')
road_net = gdf_from_sumo_network(net)
G = from_sumo_to_igraph_network(net)

Now some operations are done on the road dataframe. First, for each zone it's useful to have its zone. For the road without zone, I decided to drop them.<br>
Then, the opposite, it's easier to have zones with at least one represented road, so I decided to drop from the zones the one without a road. <br>
Lastly, I decided to extract, for each zone, its neighbors. Since one of the task is to retrieve the time needed for a user to exit from the neighborhood, <br>
it's easier to have a list of the adjecent zones ready at the use.

In [9]:
road_net = road_net.sjoin(zones_leuven, how = 'inner')[['id', 'geometry', 'CODSEC']]

In [10]:
# in the same way, some of the zone may be useless, since they don't 'point' to any street
selected_zones = set(road_net['CODSEC'].tolist())
indexs_to_drop = []

for idx, row in zones_leuven.iterrows():
    if row['CODSEC'] not in selected_zones:
        indexs_to_drop.append(idx)

zones_leuven.drop(indexs_to_drop, inplace=True)
zones_leuven.reset_index(inplace=True, drop = True)

In [11]:
hubs = hubs.sjoin(zones_leuven, how = 'inner')[['nr', 'geometry', 'CODSEC']]
hubs.reset_index(inplace=True, drop = True)

In [12]:
#Popolate the geodataframe assigning, for each street, its zone, SPATIAL JOIN
nearest_edge = []

for idx, row in hubs.iterrows():
    hub = row['geometry']
    
    #nearest neighbouring edge of the hubs
    x_o, y_o = net.convertLonLat2XY(hub.x, hub.y)
    candidates_origin = net.getNeighboringEdges(x_o, y_o, r=35, includeJunctions=True)
    if len(candidates_origin) > 0:
        #origin edge
        nearest_edge.append(sorted(candidates_origin, key = lambda x: x[1])[0][0].getID())
    else:
        nearest_edge.append('NONE') #shouldn't happen, every hub should have a neighbouring edge

hubs['Nearest edge'] = nearest_edge
# drop all the 'NONE', street, all the street without a zone
hubs.drop(list(np.where(hubs['Nearest edge'] == 'NONE')[0]), axis = 0, inplace=True)

In [13]:
# retrieve adjacent zones, by zone
adjacent_zones = []

for idx, row in zones_leuven.iterrows():
    zones_row = []
    ids = set(np.where(zones_leuven['geometry'].intersection(zones_leuven['geometry'][idx]))[0]) - set([idx]) # remove the current zone from the list
    for id in ids:
        zones_row.append(zones_leuven['CODSEC'][id])

    adjacent_zones.append(zones_row)

zones_leuven['adjacent'] = adjacent_zones

In [76]:
folium.GeoJson(road_net).add_to(m)
m

In [14]:
fdf = pd.read_csv('flussi_per_simulazione.csv')[['CODSEC_ORIG', 'CODSEC_DEST', 'flows_car_aggr', 'flows_pae_aggr']]

# Create Traffic demand <br>


In [15]:
# Create a traffic demand for the sumo network. 
# Starting from an hub configuration dataframe (points) compute two types of flows:
#   1) towards a random point outside its neighborhood (defined as one random edge in the adjacent zones)
#   2) towards the city center (defined ad-hoc)
# The process is repeated n (default = 500) times and in the end all the trips are written in the xml file in the Sumo folder.
# In this case, I decided to create all vehicles of the same types, the speed is set to
# Currently, the paths are computed as shortest path or, with a higher computational cost, using path randomization. 
# @input hubs: geodataframe with the hubs (points) configuration
# @input fast: boolean value to decide if use shorted past or random graph
# @input n: number of trips to generate

def create_demand_flows(hubs, fast = False, n = 100):

    # city center information
    city_center = (4.70110, 50.87993)
    x_c, y_c = net.convertLonLat2XY(city_center[0], city_center[1])
    candidates_center = net.getNeighboringEdges(x_c, y_c, r=25, includeJunctions=True)
    e_center = sorted(candidates_center, key = lambda x: x[1])[0][0].getID()

    i = 0
    random_destination = ''
    center_destination = ''

    print('start generation phase...', end='')
    
    while i < n:
        #get a random mobility hub -- starting point
        random_hub = hubs.sample(1)
        
        #get its zone
        start_zone = random_hub['CODSEC'].values[0]

        #select one zone of its neighbor zone
        neighbors = zones_leuven[zones_leuven['CODSEC'] == start_zone]['adjacent'].values[0]
        dest_zone = np.random.choice(neighbors)
        #destination point 1 -- random street in another zone
        destination = road_net[road_net['CODSEC'] == dest_zone].sample(1)['id'].values[0]
        #destination point2 -- city center

        #nearest neighbouring edge of the origin
        origin = random_hub['Nearest edge'].values[0]

        if not net.getOptimalPath(net.getEdge(origin), net.getEdge(destination)):
            print('c')
            continue

        random_destination += '<flow id = "r'+str(i)+'" begin="0" end = "500" departLane="random" number = "5" from = "'+origin+'" to = "'+destination+'" type="type1"></flow> \n'
        center_destination += '<flow id = "c'+str(i)+'" begin="0" end = "500" departLane="random" number = "5" from = "'+origin+'" to = "'+e_center+'" type="type1"></flow> \n'
        i +=1

    
    print('end')
    print('start writing file...', end='')
    # write the file
    f = open("Sumo/my_trips.xml", "w")
    f.write('<?xml version="1.0" encoding="UTF-8"?> <routes> <vType id="type1" length="5.00" maxSpeed="70.00" accel="2.6" decel="4.5" sigma="0.5" /> \n')
    f.write(random_destination)
    f.write(center_destination)
    f.write('</routes>')
    f.close()
    print('end')
    

## Duarouter

In [16]:
import subprocess

In [17]:
command_str = "duarouter --route-files Sumo/my_trips.xml --net-file Sumo/osm.net.xml " +\
                "--ignore-routing-errors true "+\
                "--output-file Sumo/traffic_demand_duarouter.rou.xml"

# SUMO

In [18]:
# import the traci library
import traci
import sys

In [23]:
# check sumo enviroment
if 'SUMO_HOME' in os.environ:
    tools = os.path.join(os.environ['SUMO_HOME'], 'tools')
    sys.path.append(tools)
else:
    sys.exit("please declare environment variable 'SUMO_HOME'")

#Configuration 
sumo_binary = os.environ['SUMO_HOME']+"/bin/sumo"

#command for the simulation -- use duarouter
sumo_cmd = [sumo_binary, "-c", os.getcwd()+'/Sumo/my_config_duarouter.sumocfg', '-W', 'true', '--time-to-teleport', '5', '--no-step-log',
            '-v', 'false', '-t', 'false']

In [25]:
# Main loop 
# generate a traffic demand, call duarouter for things, run the simulation. Repeat the process n times and 
# compute the average times.
# @input: hubs, geodataframe with the hub configuration
# @output: random_average_time, average time, between all the simulation and all the different users, starting
#           from a random hub to exit from its neighborhood
# @output: center_average_time, average time, between all the simulation and all the different users, starting
#           from a random hub to reach the city center

def main_loop(hubs):
    random_average_time = []
    center_average_time = []

    #traci.vehicle.subsc

    for i in range(10):
        print('-------------')
        print('iteration ', i+1)

        #create random traffic demand
        create_demand_flows(hubs, fast = True)

        #duarouter
        print('start duarouter...', end= '')
        p = subprocess.Popen(command_str, shell=True, stdout=subprocess.PIPE, 
                                        stderr=subprocess.STDOUT)
        p.wait()
        print('end')

        #start new simulation
        print('start simulation...')
        traci.start(sumo_cmd)

        print('    Starting time: 0')
        random_time = dict()
        center_time = dict()

        #run simulation until no more vehicles
        while traci.simulation.getTime() < 500 or len(traci.vehicle.getIDList()) > 0 :
            traci.simulationStep()

            #get, for each vehicle, its last travel time, divided by destinaton
            for v in traci.vehicle.getIDList():
                distance = traci.vehicle.getDistance(v)
                time = traci.simulation.getTime()
                if distance == 0:
                    distance = 1

                timebydist = time/1
                if v[0] == 'r':
                    #normalize the time based on the distance
                    random_time[v] = timebydist
                else:
                    center_time[v] = timebydist

        print('    Ending time: ', traci.simulation.getTime())
        random_average_time.append(np.mean(list(random_time.values()))/60)
        center_average_time.append(np.mean(list(center_time.values()))/60)
        print('end')

        #close the simulation
        traci.close()
        #see if i can remove the output of traci
    return np.mean(random_average_time), np.mean(center_average_time)

## Real HUBS

In [26]:
random_mean, center_mean = main_loop(hubs)

-------------
iteration  1
start generation phase...end
start writing file...end
start duarouter...end
start simulation...
 Retrying in 1 seconds
    Starting time: 0
    Ending time:  1485.0
end
-------------
iteration  2
start generation phase...end
start writing file...end
start duarouter...end
start simulation...
 Retrying in 1 seconds
    Starting time: 0
    Ending time:  1485.0
end
-------------
iteration  3
start generation phase...end
start writing file...end
start duarouter...end
start simulation...
 Retrying in 1 seconds
    Starting time: 0
    Ending time:  1485.0
end
-------------
iteration  4
start generation phase...end
start writing file...end
start duarouter...end
start simulation...
 Retrying in 1 seconds
    Starting time: 0
    Ending time:  1485.0
end
-------------
iteration  5
start generation phase...end
start writing file...end
start duarouter...end
start simulation...
 Retrying in 1 seconds
    Starting time: 0
    Ending time:  1485.0
end
-------------
iterat

In [27]:
random_mean, center_mean

(6.321633333333333, 13.135700000000003)

## Random Hubs

In [76]:
# random hubs --> random street, centroid
np.random.seed(42)
r_hubs = road_net.sample(len(hubs), replace= True)

In [82]:
r_hubs.columns = ['Nearest edge', 'geometry', 'CODSEC']

In [84]:
random_mean, center_mean = main_loop(r_hubs)

-------------
iteration  1
start generation phase...end
start writing file...end
start duarouter...end
start simulation... Retrying in 1 seconds
***Starting server on port 49596 ***
Loading net-file from '/Users/andreafrasson/Desktop/Geospatial-Analitics/Sumo/osm.net.xml.gz' ... done (706ms).
Loading additional-files from '/Users/andreafrasson/Desktop/Geospatial-Analitics/Sumo/osm.poly.xml.gz' ... done (2740ms).
Loading done.
Simulation version 1.19.0 started with time: 0.00.
end
Simulation ended at time: 2133.00
Reason: TraCI requested termination.
Performance: 
 Duration: 39.30s
 TraCI-Duration: 31.39s
 Real time factor: 54.2817
 UPS: 14169.792594
Vehicles: 
 Inserted: 1000
 Running: 0
 Waiting: 0
 Teleports: 1 (Yield: 1)
Statistics (avg of 1000):
 RouteLength: 3037.33
 Speed: 6.83
 Duration: 556.80
 WaitingTime: 159.91
 TimeLoss: 278.61
 DepartDelay: 6.35

-------------
iteration  2
start generation phase...end
start writing file...end
start duarouter...end
start simulation... Retry

In [104]:
random_mean, center_mean

(6.6342333333333325, 16.146266666666666)

## Optimal Placement

In [90]:
opt_hubs = gpd.read_file('opt_hubs.gpkg')[['geometry', 'index']]

In [93]:
opt_hubs = opt_hubs.sjoin(zones_leuven, how = 'inner')[['index', 'geometry', 'CODSEC']]
opt_hubs.reset_index(inplace=True, drop = True)

In [95]:
#Popolate the geodataframe assigning, for each street, its zone, SPATIAL JOIN
nearest_edge = []

for idx, row in opt_hubs.iterrows():
    hub = row['geometry']
    
    #nearest neighbouring edge of the opt_hubs
    x_o, y_o = net.convertLonLat2XY(hub.x, hub.y)
    candidates_origin = net.getNeighboringEdges(x_o, y_o, r=35, includeJunctions=True)
    if len(candidates_origin) > 0:
        #origin edge
        nearest_edge.append(sorted(candidates_origin, key = lambda x: x[1])[0][0].getID())
    else:
        nearest_edge.append('NONE') #shouldn't happen, every hub should have a neighbouring edge

opt_hubs['Nearest edge'] = nearest_edge
# drop all the 'NONE', street, all the street without a zone
opt_hubs.drop(list(np.where(opt_hubs['Nearest edge'] == 'NONE')[0]), axis = 0, inplace=True)

In [97]:
random_mean, center_mean = main_loop(opt_hubs)

-------------
iteration  1
start generation phase...end
start writing file...end
start duarouter...end
start simulation... Retrying in 1 seconds
***Starting server on port 49658 ***
Loading net-file from '/Users/andreafrasson/Desktop/Geospatial-Analitics/Sumo/osm.net.xml.gz' ... done (720ms).
Loading additional-files from '/Users/andreafrasson/Desktop/Geospatial-Analitics/Sumo/osm.poly.xml.gz' ... done (2705ms).
Loading done.
Simulation version 1.19.0 started with time: 0.00.
end
Simulation ended at time: 882.00
Reason: TraCI requested termination.
Performance: 
 Duration: 13.17s
 TraCI-Duration: 6.81s
 Real time factor: 66.9653
 UPS: 9270.974110
Vehicles: 
 Inserted: 398
 Running: 0
 Waiting: 0
Statistics (avg of 398):
 RouteLength: 2159.24
 Speed: 7.16
 Duration: 306.80
 WaitingTime: 21.09
 TimeLoss: 78.84
 DepartDelay: 5.50

-------------
iteration  2
start generation phase...end
start writing file...end
start duarouter...end
start simulation... Retrying in 1 seconds
***Starting ser

In [98]:
random_mean, center_mean 

(0.004730390467381084, 0.004409972307601703)